In [ ]:
import torch

# Confirm that the GPU is detected

assert torch.cuda.is_available()

# Get the GPU device name.

device_name = torch.cuda.get_device_name()
n_gpu = torch.cuda.device_count()
print(f"Found device: {device_name}, n_gpu: {n_gpu}")
device = torch.device("cuda")

# device = torch.device("mps")

Found device: NVIDIA GeForce RTX 3070 Laptop GPU, n_gpu: 1


In [ ]:
!pip install torch
!pip install transformers
!pip install -U -q PyDrive
!pip install datasets
!pip install seqeval
!pip install ray[tune]

In [ ]:
import os
import itertools
import pandas as pd
import numpy as np
from datasets import Dataset
from datasets import load_metric
from transformers import AutoTokenizer
from transformers import AutoModelForTokenClassification, TrainingArguments, Trainer
from transformers import DataCollatorForTokenClassification
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer = AutoTokenizer.from_pretrained("nlpaueb/legal-bert-base-uncased")
model = AutoModelForSequenceClassification.from_pretrained("nlpaueb/legal-bert-base-uncased", num_labels=15) # num_labels = 14 + 1


Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.decoder.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification wer

# Importing Datasets

In [ ]:
import pandas as pd

# from google.colab import drive
# drive.mount('/content/drive')
# %cd /content/drive/My Drive/Colab Notebooks/

import json

# from datasets import load_dataset, concatenate_datasets, Features, Value, ClassLabel, Sequence
# dataset = load_dataset('json', data_files='NER_JUDGEMENT_WikiAnn_Format.json')

import pandas as pd
train_df_judgement = pd.read_json('NER_TRAIN_JUDGEMENT_PREPROCESSED.json')
train_df_preamble = pd.read_json('NER_TRAIN_PREAMBLE_PREPROCESSED.json')

test_df_judgement = pd.read_json('NER_DEV_JUDGEMENT_PREPROCESSED.json')
test_df_preamble = pd.read_json('NER_DEV_PREAMBLE_PREPROCESSED.json')


In [ ]:
print(len(train_df_judgement), len(train_df_preamble))
print(len(test_df_judgement), len(test_df_preamble))
total_data = len(train_df_judgement) + len(train_df_preamble) + len(test_df_judgement) + len(test_df_preamble)

8494 553
839 28


In [ ]:
# concatenating the judgement + preamble data
df = pd.concat([train_df_judgement, train_df_preamble])
df.reset_index(inplace=True, drop=True)
# print(df)
print(total_data)
# splitting train (70% of the total data)
split=int(total_data*0.7)
split_70=split /(len(train_df_judgement) + len(train_df_preamble))
train_df = df.sample(frac = split_70)
# train_df = df[:split]
# splitting validation (appx 20% of the total data)
val_df = df.drop(train_df.index)
# val_df = df[split:]
# test data (appx 10% of the total data)
test_df = pd.concat([test_df_judgement, test_df_preamble])

9914


In [ ]:
len(train_df)

6939

In [ ]:
len(val_df)

2108

In [ ]:
train_dataset = Dataset.from_pandas(train_df)
val_dataset = Dataset.from_pandas(val_df)
test_dataset = Dataset.from_pandas(test_df)

# Tokenization

In [ ]:
labels_list = ["OTHERS", "PETITIONER", "COURT", "RESPONDENT", "JUDGE", "OTHER_PERSON", "LAWYER", "DATE", "ORG", "GPE", "STATUTE", "PROVISION", "PRECEDENT", "CASE_NUMBER", "WITNESS"]
label_encoding_dict = {0: 0, 1: 1, 2: 2, 3: 3, 4: 4, 5: 5, 6: 6, 7: 7, 8: 8, 9: 9, 10: 10, 11: 11, 12: 12, 13: 13, 14: 14}
label_list_encoding_dict = {0: "OTHERS", 1: "PETITIONER", 2: "COURT", 3: "RESPONDENT", 4: "JUDGE", 5: "OTHER_PERSON", 6: "LAWYER", 7: "DATE", 8: "ORG", 9: "GPE", 10: "STATUTE", 11: "PROVISION", 12: "PRECEDENT", 13: "CASE_NUMBER", 14: "WITNESS"}

In [ ]:
batch_size = 10

def tokenize_all_labels(rows):
    label_all = True
    tokenized_inputs = tokenizer(list(rows["tokens"]), truncation = True, is_split_into_words = True)
    labels = []
    for index, label in enumerate(rows["ner_tags"]):
        # print(i, label)
        previous_word_idx = None
        word_ids = tokenized_inputs.word_ids(batch_index = index)
        
        label_ids = []
        for word_idx in word_ids:
            if word_idx is None: label_ids.append(-100)
            elif label[word_idx] == '0': label_ids.append(0)
            elif word_idx != previous_word_idx: label_ids.append(label_encoding_dict[label[word_idx]])
            else: label_ids.append(label_encoding_dict[label[word_idx]] if label_all else -100)
            previous_word_idx = word_idx
        labels.append(label_ids)
        
    tokenized_inputs["labels"] = labels
    return tokenized_inputs


train_dataset_tokenized = train_dataset.map(tokenize_all_labels, batched=True)
val_dataset_tokenized = val_dataset.map(tokenize_all_labels, batched=True)

Map:   0%|          | 0/6939 [00:00<?, ? examples/s]

Map:   0%|          | 0/2108 [00:00<?, ? examples/s]

# Hyperparameter Tuning

In [ ]:
import os
# os.environ['TUNE_MAX_PENDING_TRIALS_PG'] = "1"
os.environ["TUNE_DISABLE_AUTO_CALLBACK_LOGGERS"] = "1"

In [ ]:
from ray import tune
def ray_hp_space(trial):
    return {
        "learning_rate": tune.loguniform(1e-6, 1e-4),
        "per_device_train_batch_size": tune.choice([5, 8, 10]),
        "num_train_epochs": tune.choice([5, 10, 15])
    }

In [ ]:
import warnings
warnings.filterwarnings('ignore')

metric = load_metric("seqeval")
tokenizer = AutoTokenizer.from_pretrained("nlpaueb/legal-bert-base-uncased")

def model_init():
    return AutoModelForTokenClassification.from_pretrained("nlpaueb/legal-bert-base-uncased", num_labels=len(labels_list))

training_arguments = TrainingArguments(
    "eval_indian_legal_ner",
    evaluation_strategy = "epoch",
    learning_rate=1e-6,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=1e-5,
)

data_collator = DataCollatorForTokenClassification(tokenizer)

def evaluate_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)

    actual_predictions = [[labels_list[p] for (p, l) in zip(prediction, label) if l != -100] for prediction, label in zip(predictions, labels)]
    actual_labels = [[labels_list[l] for (p, l) in zip(prediction, label) if l != -100] for prediction, label in zip(predictions, labels)]
    results = metric.compute(predictions=actual_predictions, references=actual_labels)
    return {"precision": results["overall_precision"], "recall": results["overall_recall"], "f1": results["overall_f1"], "accuracy": results["overall_accuracy"]}

def compute(metrics):
    return metrics["eval_accuracy"]
    
trainer = Trainer(
    model=None,
    args = training_arguments,
    train_dataset = train_dataset_tokenized,
    eval_dataset = val_dataset_tokenized,
    data_collator = data_collator,
    tokenizer = tokenizer,
    model_init = model_init,
    compute_metrics = evaluate_metrics
)
best_trial = trainer.hyperparameter_search(
    direction="maximize",
    backend="ray",
    hp_space=ray_hp_space,
    n_trials=6,
    compute_objective=compute
)

Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForTokenClassification: ['cls.predictions.decoder.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initia

== Status ==
Current time: 2023-05-17 13:17:45 (running for 00:00:00.07)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-17_13-17-44
Number of trials: 6/6 (5 PENDING, 1 RUNNING)
+------------------------+----------+----------------+-----------------+--------------------+------------------------+
| Trial name             | status   | loc            |   learning_rate |   num_train_epochs |   per_device_train_bat |
|                        |          |                |                 |                    |                ch_size |
|------------------------+----------+----------------+-----------------+--------------------+------------------------|
| _objective_bd081_00000 | RUNNING  | 127.0.0.1:8672 |     5.61152e-06 |                 15 |                      5 |
| _objective_bd081_00001 | PENDING  |                |     2.91064e-05 |                  5 |                      5 |
| _objective_b

(_objective pid=8672) Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForTokenClassification: ['cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
(_objective pid=8672) - This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
(_objective pid=8672) - This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification 

== Status ==
Current time: 2023-05-17 13:17:57 (running for 00:00:12.16)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-17_13-17-44
Number of trials: 6/6 (5 PENDING, 1 RUNNING)
+------------------------+----------+----------------+-----------------+--------------------+------------------------+
| Trial name             | status   | loc            |   learning_rate |   num_train_epochs |   per_device_train_bat |
|                        |          |                |                 |                    |                ch_size |
|------------------------+----------+----------------+-----------------+--------------------+------------------------|
| _objective_bd081_00000 | RUNNING  | 127.0.0.1:8672 |     5.61152e-06 |                 15 |                      5 |
| _objective_bd081_00001 | PENDING  |                |     2.91064e-05 |                  5 |                      5 |
| _objective_b

  0%|          | 76/20820 [00:06<30:35, 11.30it/s]


...

== Status ==
Current time: 2023-05-17 15:03:12 (running for 01:45:26.68)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-17_13-17-44
Number of trials: 6/6 (1 ERROR, 1 RUNNING, 4 TERMINATED)
+------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------+
| Trial name             | status     | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |   objective |
|                        |            |                 |                 |                    |                ch_size |             |
|------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------|
| _objective_bd081_00005 | RUNNING    | 127.0.0.1:15028 |     2.65875e-06 |                  5 |                      5 |    0.945692 |
| _objective_bd081_00000 | TERMINATE

(_objective pid=15028) C:\Users\kavya\AppData\Local\Programs\Python\Python38\lib\site-packages\seqeval\metrics\v1.py:57: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
(_objective pid=15028)   _warn_prf(average, modifier, msg_start, len(result))


== Status ==
Current time: 2023-05-17 15:03:13 (running for 01:45:27.95)
Using FIFO scheduling algorithm.
Logical resource usage: 0/16 CPUs, 0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-17_13-17-44
Number of trials: 6/6 (1 ERROR, 5 TERMINATED)
+------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------+
| Trial name             | status     | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |   objective |
|                        |            |                 |                 |                    |                ch_size |             |
|------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------|
| _objective_bd081_00000 | TERMINATED | 127.0.0.1:8672  |     5.61152e-06 |                 15 |                      5 |    0.965036 |
| _objective_bd081_00001 | TERMINATED | 127.0.0.1:2

                                                   
100%|██████████| 6940/6940 [10:43<00:00, 10.78it/s]


TuneError: ('Trials did not complete', [_objective_bd081_00002])

In [1]:
    # The best trial run has the hyperparameters = {
                                                  # 'learning_rate': 2.910635913133073e-05, 
                                                  # 'per_device_train_batch_size': 5, 
                                                  # 'num_train_epochs': 5}
    # One trial errored out so we are ignoring this trial run.
    # (ERROR: attention_scores = torch.matmul(query_layer, key_layer.transpose(-1, -2)) 
    # torch.cuda.OutOfMemoryError: CUDA out of memory.)
